In [59]:
!pip install simpy

In [60]:
import simpy
import numpy as np
import numpy.random as random
import math

In [61]:
MAXSIMTIME = 50000
VERBOSE = False
LAMBDA = 2.0
MU = 1.0
POPULATION = 50000000
SERVICE_DISCIPLINE = 'FIFO'
LOGGED = True
PLOTTED = True
NUM_OF_TICKET_COLLECTOR = 3
NUM_OF_TABLE = 10
NUM_OF_FOOD_TABLE = 5
QUITING_RATE_AFTER_TICKET_COLLECTOR = 0.3
QUITING_RATE_AFTER_TABLE_SETTER = 0.2
BACK_TO_FOOD_TABLE_RATE = 0.5

In [62]:
VERBOSE = True  # In thông tin chi tiết nếu được kích hoạt

class Customer:
    def __init__(self, name, arrtime):
        self.name = name
        self.arrtime = arrtime

    def __str__(self):
        return '%s arrived at %.2f' % (self.name, self.arrtime)

class CustomerGenerator:
    def __init__(self, env, queuegate, arrival_rate=5):
        self.interarrival_time = 1 / arrival_rate
        self.queuegate = queuegate
        env.process(self.generate_customers(env))

    def generate_customers(self, env):
        customer_count=0
        while True:
            
            # Tạo thời gian đến cho khách hàng
            customer_interarrival = random.exponential(self.interarrival_time)
            yield env.timeout(customer_interarrival)

            # Tạo khách hàng mới
            customer = Customer('Customer %s' % customer_count, env.now)
            # Thêm khách hàng vào hàng đợi
                
            self.queuegate.Customers.append( customer )
            env.process(self.queuegate.serve())
            customer_count +=1
            if not self.queuegate.serversleeping.triggered:
                self.queuegate.serversleeping.interrupt( 'Wake up, please.' )
            


In [43]:
VERBOSE = True  # In thông tin chi tiết nếu được kích hoạt
class QueueGate:
    def __init__(self, env, servers, servicetime, queuetable, ratequit, strat='FIFO'):
        self.env = env
        self.Servers = simpy.Resource(env, servers)
        self.numOfServers = servers
        self.servicetime = servicetime
        self.strat = strat
        self.Customers = list(())
        self.queuetable = queuetable
        self.ratequit = ratequit
        self.serversleeping = None
        ''' statistics '''
        self.waitingTime = 0
        self.idleTime = 0
        self.customerDone = 0
        env.process(self.serve())

    def serve(self):
            print('Num of customers waiting at gate : %d' %(len(self.Customers)))
            if(len(self.Customers)) == 0:
                self.serversleeping = self.env.process( self.waiting())
                t1 = self.env.now
                yield self.serversleeping
                ''' accumulate the server idle time'''
                self.idleTime += self.env.now - t1
            else:
                '''check if server is full or not'''
                with self.Servers.request() as req:
                    yield req
                    self.numOfServers -=1
                    '''Start being serve'''
                    if(len(self.Customers)>0):
                        customer = self.Customers.pop(0)
                        time_served = self.env.now
                        
                        if VERBOSE: 
                            print('%s: - Start being served at gate -  %.2f' % (customer, time_served))
                            print('- Num of collectors left at gate: %d' % (self.numOfServers))

                        '''caculate time waiting for each customer'''
                        self.waitingTime += time_served - customer.arrtime 
                        
                        '''serve customer'''
                        yield self.env.timeout(random.exponential( self.servicetime ))
                        if VERBOSE: print('%s: - Done being served - leaving gate -  %.2f' % (customer, self.env.now))
                        '''sum total customer done'''
                        self.customerDone += 1
                        customer.arrtime = self.env.now
                        '''quit rate of customer'''
                        if(random.random() > self.ratequit):
                            self.queuetable.Customers.append( customer )
                            self.env.process(self.queuetable.serve())
                        else: print('%s quit out' % (customer))

                        self.numOfServers += 1
                    else:
                       self.numOfServers += 1 
                    if LOGGED:
                        qlog.write( '- Gate: %.4f \t %d \t %d \t %d \n' % (self.env.now, 1 if len(self.Customers)>0 else 0, len(self.Customers), self.numOfServers ))
                     
    def waiting(self):
        try:
            if VERBOSE: 
                print('- Num of free gate collectors: %d' % (self.numOfServers))     
            yield self.env.timeout( MAXSIMTIME )
        except simpy.Interrupt as i:
            if VERBOSE:
                print(' gate collector works again at %.2f' % self.env.now )


        
    

In [44]:
class QueueSetTable:
    def __init__(self, env, servers, servicetime, queuegetfood, ratequit, strat='FIFO'):
        self.env = env
        self.Servers = simpy.Resource(env, servers)
        self.numOfServers = servers
        self.servicetime = servicetime
        self.strat = strat
        self.Customers = list(())
        self.queuegetfood = queuegetfood
        self.ratequit = ratequit
        self.serversleeping = None
        ''' statistics '''
        self.waitingTime = 0
        self.idleTime = 0
        self.customerDone = 0
        env.process(self.serve())

    def serve(self):
            print('Num of customers waiting at setting table : %d' %(len(self.Customers)))
            if(len(self.Customers)) == 0:
                self.serversleeping = self.env.process( self.waiting())
                t1 = self.env.now
                yield self.serversleeping
                ''' accumulate the server idle time'''
                self.idleTime += self.env.now - t1
            else:
                '''check if server is full or not'''
                with self.Servers.request() as req:
                    yield req
                    self.numOfServers -=1
                    '''Start being serve'''
                    if(len(self.Customers)>0):
                        customer = self.Customers.pop(0)
                        time_served = self.env.now
                        # if LOGGED:
                        #     qlog.write( '%.4f \t %d \t %d \t %d \n' % (self.env.now, 1 if len(self.Customers)>0 else 0, len(self.Customers), self.numOfServers ))
                        if VERBOSE:
                            print('%s: - Start being served at setting table -  %.2f' % (customer, time_served))
                            print('- Num of free table at setting table: %d' % (self.numOfServers))

                        '''caculate time waiting for each customer'''
                        self.waitingTime += time_served - customer.arrtime

                        '''serve customer'''
                        yield self.env.timeout(random.exponential( self.servicetime ))
                        if VERBOSE: print('%s: - Done being served - leaving setting table - %.2f' % (customer, self.env.now))
                        '''sum total customer done'''
                        self.customerDone += 1
                        customer.arrtime = self.env.now
                        '''quit rate of customer'''
                        if(random.random() > self.ratequit):
                            self.queuegetfood.Customers.append( customer )
                            self.env.process(self.queuegetfood.serve())
                        else: print('%s quit out' % (customer))
                        self.numOfServers += 1
                    else:
                       self.numOfServers += 1
                    if LOGGED:
                        qlog.write( '- Table: %.4f \t %d \t %d \t %d \n' % (self.env.now, 1 if len(self.Customers)>0 else 0, len(self.Customers), self.numOfServers ))

    def waiting(self):
        try:
            if VERBOSE:
                print('- Num of free table at setting table: %d' % (self.numOfServers))
            yield self.env.timeout( MAXSIMTIME )
        except simpy.Interrupt as i:
            if VERBOSE:
                print('Table being set at %.2f' % self.env.now )

                

In [45]:

class QueueGetFood:
    def __init__(self, env, servers, servicetime, totalservedcustomers, ratereturn, strat='FIFO'):
        self.env = env
        self.Servers = simpy.Resource(env, servers)
        self.numOfServers = servers
        self.servicetime = servicetime
        self.strat = strat
        self.Customers = list(())
        self.totalservedcustomers = totalservedcustomers
        self.ratereturn = ratereturn
        self.serversleeping = None
        ''' statistics '''
        self.waitingTime = 0
        self.idleTime = 0
        self.customerDone = 0
        env.process(self.serve())

    def serve(self):
            print('Num of customers waiting at food table : %d' %(len(self.Customers)))
            if(len(self.Customers)) == 0:
                self.serversleeping = self.env.process( self.waiting())
                t1 = self.env.now
                yield self.serversleeping
                ''' accumulate the server idle time'''
                self.idleTime += self.env.now - t1
            else:
                '''check if server is full or not'''
                with self.Servers.request() as req:
                    yield req
                    self.numOfServers -=1
                    '''Start being serve'''
                    if(len(self.Customers)>0):
                        customer = self.Customers.pop(0)
                        time_served = self.env.now
                        # if LOGGED:
                        #     qlog.write( '%.4f \t %d \t %d \t %d \n' % (self.env.now, 1 if len(self.Customers)>0 else 0, len(self.Customers), self.numOfServers ))
                        if VERBOSE:
                            print('%s: - Start choosing food at food table -  %.2f' % (customer, time_served))
                            print('- Num of table left at food table: %d' % (self.numOfServers))

                        '''caculate time waiting for each customer'''
                        self.waitingTime += time_served - customer.arrtime

                        '''serve customer'''
                        yield self.env.timeout(random.exponential( self.servicetime ))
                        if VERBOSE: print('%s: - Done choosing food - leaving food table - %.2f' % (customer, self.env.now))
                        '''sum total customer done'''
                        self.customerDone += 1
                        customer.arrtime = self.env.now
                        '''quit rate of customer'''
                        if(random.random() < self.ratereturn):
                            print('%s choosing food again' % (customer))
                            self.Customers.append( customer )
                            self.env.process(self.serve())
                        else:
                            self.totalservedcustomers.append(customer )
                            print('%s leave the restaurant' % (customer))
                        self.numOfServers += 1
                    else:
                       self.numOfServers += 1
                    if LOGGED:
                        qlog.write( '- Food: %.4f \t %d \t %d \t %d \n' % (self.env.now, 1 if len(self.Customers)>0 else 0, len(self.Customers), self.numOfServers ))

    def waiting(self):
        try:
            if VERBOSE:
                print('- Num of table free at food table: %d' % (self.numOfServers))
            yield self.env.timeout( MAXSIMTIME )
        except simpy.Interrupt as i:
            if VERBOSE:
                print('Food table is choosen and serves at %.2f' % self.env.now )
     
        


In [46]:
if LOGGED:
    qlog = open( 'mm1-l%d-m%d.csv' % (LAMBDA,MU), 'w' )
    qlog.write( '0\t0\t0\n' )

In [47]:
env2 = simpy.Environment()

total_served_customers = list(())

MyQueueGetFood = QueueGetFood(env2, NUM_OF_FOOD_TABLE, MU, total_served_customers, BACK_TO_FOOD_TABLE_RATE, SERVICE_DISCIPLINE)
MyQueueSetTable = QueueSetTable( env2, NUM_OF_TABLE, MU, MyQueueGetFood, QUITING_RATE_AFTER_TABLE_SETTER, SERVICE_DISCIPLINE)
MyQueueGate = QueueGate( env2, NUM_OF_TICKET_COLLECTOR, MU, MyQueueSetTable, QUITING_RATE_AFTER_TICKET_COLLECTOR, SERVICE_DISCIPLINE)
MyJobGenerator = CustomerGenerator( env2, MyQueueGate, LAMBDA)



In [48]:
MAXSIMTIME2 = 100000
print (env2.now)

0


In [49]:
env2.run( until = MAXSIMTIME)
print (env2.now)
print ("num of customer serve %d" %(len(total_served_customers)))

Num of customers waiting at food table : 0
Num of customers waiting at setting table : 0
Num of customers waiting at gate : 0
- Num of table free at food table: 5
- Num of free table at setting table: 10
- Num of free gate collectors: 3
Num of customers waiting at gate : 1
 gate collector works again at 0.22
Customer 0 arrived at 0.22: - Start being served at gate -  0.22
- Num of collectors left at gate: 2
Num of customers waiting at gate : 1
Customer 1 arrived at 0.29: - Start being served at gate -  0.29
- Num of collectors left at gate: 1
Num of customers waiting at gate : 1
Customer 2 arrived at 0.31: - Start being served at gate -  0.31
- Num of collectors left at gate: 0
Customer 0 arrived at 0.22: - Done being served - leaving gate -  0.52
Customer 0 arrived at 0.52 quit out
Num of customers waiting at gate : 1
Customer 3 arrived at 0.57: - Start being served at gate -  0.57
- Num of collectors left at gate: 0
Customer 2 arrived at 0.31: - Done being served - leaving gate -  0.

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



Num of customers waiting at food table : 1
Customer 35120 arrived at 17581.18: - Start choosing food at food table -  17581.18
- Num of table left at food table: 2
Num of customers waiting at gate : 2
Customer 35117 arrived at 17579.48: - Done choosing food - leaving food table - 17581.45
Customer 35117 arrived at 17581.45 choosing food again
Num of customers waiting at food table : 1
Customer 35117 arrived at 17581.45: - Start choosing food at food table -  17581.45
- Num of table left at food table: 2
Customer 35117 arrived at 17581.45: - Done choosing food - leaving food table - 17581.63
Customer 35117 arrived at 17581.63 leave the restaurant
Customer 35124 arrived at 17579.42: - Done being served - leaving gate -  17581.68
Num of customers waiting at setting table : 1
Customer 35124 arrived at 17581.68: - Start being served at setting table -  17581.68
- Num of free table at setting table: 9
Customer 35125 arrived at 17580.88: - Start being served at gate -  17581.68
- Num of colle

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



Num of customers waiting at setting table : 1
Customer 68955 arrived at 34534.21: - Start being served at setting table -  34534.21
- Num of free table at setting table: 7
Customer 68952 arrived at 34533.84: - Done being served - leaving setting table - 34534.27
Num of customers waiting at food table : 1
Customer 68952 arrived at 34534.27: - Start choosing food at food table -  34534.27
- Num of table left at food table: 1
Customer 68954 arrived at 34533.40: - Done being served - leaving gate -  34534.37
Customer 68954 arrived at 34534.37 quit out
Num of customers waiting at gate : 1
Customer 68956 arrived at 34534.54: - Start being served at gate -  34534.54
- Num of collectors left at gate: 2
Customer 68955 arrived at 34534.21: - Done being served - leaving setting table - 34534.60
Num of customers waiting at food table : 1
Customer 68955 arrived at 34534.60: - Start choosing food at food table -  34534.60
- Num of table left at food table: 0
Customer 68952 arrived at 34534.27: - Don

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



In [50]:
if LOGGED:
    qlog.close()

Nếu cường độ lưu lượng lớn hơn một thì hàng đợi sẽ tăng lên không giới hạn nhưng nếu việc sử dụng máy chủ p = lamda/(c*MU) < 1 thì hệ thống có phân bố dừng với hàm khối lượng xác suất, hàm đó là Stationary probabilities p(0) được tính ở bên dưới.

In [63]:
# Tính toán Utilization p
# p = RHO = LAMBDA / (MU*c) trong đó c là số server của mỗi quá trình
# QueueGate sẽ có LAMBDA = 2.0, MU = 1.0
# QueueSetTable sẽ có LAMBDA = 0.7*2, MU = 1.0
# QueueGetFood sẽ có LAMBDA = (0.8*0.7*2)/(0.5), MU = 1.0
# Tính toán số khách hàng trung bình trong hàng đợi
p_QueueGate_Theory = (LAMBDA / (MU * NUM_OF_TICKET_COLLECTOR))
p_QueueSetTable_Theory = (LAMBDA*(1-QUITING_RATE_AFTER_TICKET_COLLECTOR)) / (MU * NUM_OF_TABLE)
p_QueueGetFood_Theory = (LAMBDA*(1-QUITING_RATE_AFTER_TICKET_COLLECTOR)*(1-QUITING_RATE_AFTER_TABLE_SETTER) / ((MU * NUM_OF_FOOD_TABLE)*(1-BACK_TO_FOOD_TABLE_RATE)))
# In Utilization của từng quá trình 
print ('Utilization Theory of QueueGate : %.2f' % p_QueueGate_Theory)
print ('Utilization Theory of QueueSetTable : %.2f' % p_QueueSetTable_Theory)
print ('Utilization Theory of QueueGetFood : %.2f' % p_QueueGetFood_Theory)


Utilization Theory of QueueGate : 0.67
Utilization Theory of QueueSetTable : 0.14
Utilization Theory of QueueGetFood : 0.45


In [67]:
#Tính Stationary probabilities p(0)
def SigmaQueueGate(x):
    return ((NUM_OF_TICKET_COLLECTOR * p_QueueGate_Theory)**x)/(math.factorial(x))
def SigmaQueueSetTable(x):
    return ((NUM_OF_TABLE * p_QueueSetTable_Theory)**x)/(math.factorial(x))
def SigmaQueueGetFood(x):
    return ((NUM_OF_FOOD_TABLE * p_QueueGetFood_Theory)**x)/(math.factorial(x))
def sigma(func, frm, to):
    result = 0
    for i in range(frm, to+1):
        result += func(i)
    return result
sum_QueueGate = sigma(SigmaQueueGate, 0, NUM_OF_TICKET_COLLECTOR-1)
sum_QueueSetTable = sigma(SigmaQueueSetTable, 0, NUM_OF_TABLE-1)
sum_QueueGetFood = sigma(SigmaQueueGetFood, 0, NUM_OF_FOOD_TABLE-1)
p_0_QueueGate = 1 / (((p_QueueGate_Theory * NUM_OF_TICKET_COLLECTOR) ** NUM_OF_TICKET_COLLECTOR) / (math.factorial(NUM_OF_TICKET_COLLECTOR) * (1 - p_QueueGate_Theory)) + sum_QueueGate)
p_0_QueueSetTable = 1 / (((p_QueueSetTable_Theory * NUM_OF_TABLE) ** NUM_OF_TABLE) / (math.factorial(NUM_OF_TABLE) * (1 - p_QueueSetTable_Theory)) + sum_QueueSetTable)
p_0_QueueGetFood = 1 / (((p_QueueGetFood_Theory * NUM_OF_FOOD_TABLE) ** NUM_OF_FOOD_TABLE) / (math.factorial(NUM_OF_FOOD_TABLE) * (1 - p_QueueGetFood_Theory)) + sum_QueueGetFood)
print('Stationary probabilities of QueueGate: %.2f' % p_0_QueueGate)
print('Stationary probabilities of QueueSetTable: %.2f' % p_0_QueueSetTable)
print('Stationary probabilities of QueueGetFood: %.2f' % p_0_QueueGetFood)

Stationary probabilities of QueueGate: 0.11
Stationary probabilities of QueueSetTable: 0.25
Stationary probabilities of QueueGetFood: 0.11


In [69]:
# Tính số khách hàng trung bình trong hàng đợi L(q)
L_q_QueueGate = (p_QueueGate_Theory * ((NUM_OF_TICKET_COLLECTOR * p_QueueGate_Theory)**NUM_OF_TICKET_COLLECTOR) * p_0_QueueGate)/(math.factorial(NUM_OF_TICKET_COLLECTOR) * ((1-p_QueueGate_Theory)**2))
L_q_QueueSetTable = (p_QueueSetTable_Theory * ((NUM_OF_TABLE * p_QueueSetTable_Theory)**NUM_OF_TABLE) * p_0_QueueSetTable)/(math.factorial(NUM_OF_TABLE) * ((1-p_QueueSetTable_Theory)**2))
L_q_QueueGetFood = (p_QueueGetFood_Theory * ((NUM_OF_FOOD_TABLE * p_QueueGetFood_Theory)**NUM_OF_FOOD_TABLE) * p_0_QueueGetFood)/(math.factorial(NUM_OF_FOOD_TABLE) * ((1-p_QueueGetFood_Theory)**2))
print('Avarage number of customers in each server of QueueGate : %.2f' % L_q_QueueGate)
print('Avarage number of customers in each server of QueueSetTable : %.2f' % L_q_QueueSetTable)
print('Avarage number of customers in each server of QueueGetFood : %.2f' % L_q_QueueGetFood)

Avarage number of customers in each server of QueueGate : 0.89
Avarage number of customers in each server of QueueSetTable : 0.00
Avarage number of customers in each server of QueueGetFood : 0.07


In [76]:
# Tính số khách hàng trung bình trong hệ thống L
L_QueueGate = L_q_QueueGate + LAMBDA / MU
L_QueueSetTable = L_q_QueueSetTable + LAMBDA*(1-QUITING_RATE_AFTER_TICKET_COLLECTOR) / MU
L_QueueGetFood = L_q_QueueGetFood + LAMBDA*(1-QUITING_RATE_AFTER_TICKET_COLLECTOR)*(1-QUITING_RATE_AFTER_TABLE_SETTER) / (MU * (1 - BACK_TO_FOOD_TABLE_RATE))
print('Avarage number of customers in QueueGate : %.2f' % L_QueueGate)
print('Avarage number of customers in QueueSetTable : %.2f' % L_QueueSetTable)
print('Avarage number of customers in QueueGetFood : %.2f' % L_QueueGetFood)

Avarage number of customers in QueueGate : 2.89
Avarage number of customers in QueueSetTable : 1.40
Avarage number of customers in QueueGetFood : 2.31


In [77]:
# Tính thời gian xếp hàng trung bình của mỗi khách hàng W(q)
W_q_QueueGate = (((NUM_OF_TICKET_COLLECTOR * p_QueueGate_Theory)**NUM_OF_TICKET_COLLECTOR)*p_0_QueueGate)/(math.factorial(NUM_OF_TICKET_COLLECTOR)*NUM_OF_TICKET_COLLECTOR*MU*((1-p_QueueGate_Theory)**2))
W_q_QueueSetTable = (((NUM_OF_TABLE * p_QueueSetTable_Theory)**NUM_OF_TABLE)*p_0_QueueSetTable)/(math.factorial(NUM_OF_TABLE)*NUM_OF_TABLE*MU*((1-p_QueueSetTable_Theory)**2))
W_q_QueueGetFood = (((NUM_OF_FOOD_TABLE * p_QueueGetFood_Theory)**NUM_OF_FOOD_TABLE)*p_0_QueueGetFood)/(math.factorial(NUM_OF_FOOD_TABLE)*NUM_OF_FOOD_TABLE*MU*((1-p_QueueGetFood_Theory)**2))
print('Average time in the queue for a customer of QueueGate : %.2f' % W_q_QueueGate)
print('Average time in the queue for a customer of QueueSetTable: %.2f' % W_q_QueueSetTable)
print('Average time in the queue for a customer of QueueGetFood : %.2f' % W_q_QueueGetFood)

Average time in the queue for a customer of QueueGate : 0.44
Average time in the queue for a customer of QueueSetTable: 0.00
Average time in the queue for a customer of QueueGetFood : 0.03


In [72]:
# Tính thời gian trung bình trong hệ thống đối với một khách hàng W = W(q) + 1/MU
W_QueueGate = W_q_QueueGate + 1/MU
W_QueueSetTable = W_q_QueueSetTable + 1/MU
W_QueueGetFood = W_q_QueueGetFood + 1/MU
print('Average time in the QueueGate for a customer  : %.2f' % W_QueueGate)
print('Average time in the QueueSetTable for a customer  : %.2f' % W_QueueSetTable)
print('Average time in the QueueGetFood for a customer  : %.2f' % W_QueueGetFood)

Average time in the QueueGate for a customer  : 1.44
Average time in the QueueSetTable for a customer  : 1.16
Average time in the QueueGetFood for a customer  : 1.65


In [73]:
# Tính Utilization thực tế và Mean Waiting Time thực tế
total_idle_time = MyQueueGate.idleTime + MyQueueSetTable.idleTime + MyQueueGetFood.idleTime
total_waiting_time = MyQueueGate.waitingTime + MyQueueSetTable.waitingTime + MyQueueGetFood.waitingTime
total_customer_served = MyQueueGate.customerDone + MyQueueSetTable.customerDone + MyQueueGetFood.customerDone
print('Customer done of QueueGate : %.2f' % MyQueueGate.customerDone)
print('Customer done of QueueSetTable : %.2f' % MyQueueSetTable.customerDone)
print('Customer done of QueueGetFood : %.2f' % MyQueueGetFood.customerDone)
print('Utilization Reality : %.2f' % (1.0 - (total_idle_time / (MU * ((NUM_OF_TICKET_COLLECTOR) + (NUM_OF_TABLE) + (NUM_OF_FOOD_TABLE)))) / MAXSIMTIME))
print('Mean Waiting Time Reality : %.2f' % (total_waiting_time / total_customer_served))

Customer done of QueueGate : 99927.00
Customer done of QueueSetTable : 69984.00
Customer done of QueueGetFood : 112124.00
Utilization Reality : 1.00
Mean Waiting Time Reality : 0.17
